In [2]:
import pandas as pd
import os
os.chdir('/Users/reetb/Desktop/BTC_Prediction/data')

# Parameters
## Labeling: 
### window_l: window size for labeling.
### For every row, label = (Avg price today - Avg price window_l days back) / Avg price today 

## Features:
### window_t: window size for calculating today's trend
### window_h: window size for calculating historical trend
### look_back: frequency of look backs at historical data (90 days for quarterly, 180 days for semi-annually etc.)
### look_back_steps: total number of look backs 
### Feature vector: historical trend + today's trend + today's value
#### today's value: ['Open','High','Low','Close','Adj Close','Volume']
#### today's trend: ['Open_window_t','High_window_t','Low_window_t','Close_window_t','Adj Close_window_t','Volume_window_t'] where X_window_t = (X today - X window_l days back) / X today
#### historical trend: ['Open_l_window_h','High_l_window_h','Low_l_window_h','Close_l_window_h','Adj Close_l_window_h','Volume_l_window_h'] * S,  where X_l_window_h = (X (l * S) days back from today - X window_h days back from the (l * S) days back) / X (l * S) days back from today and S \in (1,look_back_steps)

In [17]:
## Read the dataset, convert date strings to Datetime, and use that column as index. Check for values <= 0. 

df = pd.read_csv('BTC-USD.csv')
df['Date'] = pd.to_datetime(df['Date'])
df = df.set_index('Date')
# df.loc['2023-12-26']
# df.le(0).any().any() # = False [Checked]

False

In [38]:
## Set the parameters:

window_l = 7

window_t = 30
window_h = 30

look_back = 4
look_back_steps = 8

In [37]:
## Generate the labels for each row as a separate column 'Labels'

from datetime import timedelta


df["Label"] = ''
for index, row in df.iterrows():
    if (index <= pd.to_datetime('2014-09-24')):
        df["Label"][index] = 0
    else:
        avg_today = (df['High'][index] + df['Low'][index]) / 2
        avg_window_l_back = (df['High'][index - timedelta(days = window_l)] + df['Low'][index - timedelta(days = window_l)]) / 2
        df['Label'][index] = (avg_today - avg_window_l_back) / avg_today
        

# Test to see if the labels were generated correctly based on a random day

avg_today_test = (df['High'][pd.to_datetime('2014-10-24')] + df['Low'][pd.to_datetime('2014-10-24')]) / 2
avg_window_l_back_test = (df['High'][pd.to_datetime('2014-10-24') - timedelta(days = window_l)] + df['Low'][pd.to_datetime('2014-10-24') - timedelta(days = window_l)]) / 2
if df['Label'][pd.to_datetime('2014-10-24')] == (avg_today_test - avg_window_l_back_test) / avg_today_test:
    print('Test passed. Labels generated correctly')

Test passed. Labels generated correctly


/var/folders/7f/s4xn83mn2xdfz7mzx105f0h40000gn/T/ipykernel_51046/1675802698.py:9: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df["Label"][index] = 0
/var/folders/7f/s4xn83mn2xdfz7mzx105f0h40000gn/T/ipykernel_51046/1675802698.py:9: SettingW